# Scrips para cargar la base de datos a mongodb

In [2]:
import pandas as pd
from pymongo import MongoClient

# 1. Conexión a MongoDB
cliente = MongoClient("mongodb://localhost:27017/")
db = cliente["mazatlan"]

# 2. Cargar Excel
archivo = "BD_GUIA.xlsx"
xls = pd.ExcelFile(archivo)

# 3. Cargar hojas
df_developers = xls.parse("Desarrollador")
df_developments = xls.parse("Desarrollos")
df_models = xls.parse("Modelos")
df_units = xls.parse("Unidades")

# 🔐 FUNCIONES DE CONVERSIÓN SEGURA
def safe_int(value):
    try:
        return int(value)
    except (ValueError, TypeError):
        return None

def safe_float(value):
    try:
        return float(value)
    except (ValueError, TypeError):
        return None

def safe_str(value):
    return str(value) if pd.notna(value) else ""

# 4. Subir catálogo de desarrolladores
for _, row in df_developers.iterrows():
    db.developers.update_one(
        {"developer_id": row["developer_id"]},
        {"$set": {"developer_name": row["developer_name"]}},
        upsert=True
    )

# 5. Subir desarrollos con modelos y unidades
for _, dev in df_developments.iterrows():
    dev_models = df_models[df_models["development_id"] == dev["development_id"]]
    models_list = []

    for _, model in dev_models.iterrows():
        model_units = df_units[
            (df_units["development_id"] == dev["development_id"]) &
            (df_units["model_id"] == model["model_id"])
        ]
        units_list = model_units.to_dict(orient="records")

        models_list.append({
            "model_id": safe_str(model["model_id"]),
            "model_name": safe_str(model["model_name"]),
            "total_units_by_model": safe_int(model["total_units_by_model"]),
            "bedroom_count": safe_int(model["bedroom_count"]),
            "bathroom_count": safe_float(model["bathroom_count"]),
            "parking_spaces": safe_int(model["parking_spaces"]),
            "finishes": safe_str(model["finishes"]),
            "equipment_level": safe_str(model["equipped"]),
            "units": units_list
        })

    # Construir documento del desarrollo
    doc = {
        "development_id": safe_str(dev["development_id"]),
        "development_name": safe_str(dev["development_name"]),
        "state": safe_str(dev["state"]),
        "municipality": safe_str(dev["municipality"]),
        "developer_id": safe_str(dev["developer_id"]),
        "housing_type": safe_str(dev["housing_type"]),
        "unit_count": safe_int(dev["unit_count"]),
        "model_count": safe_int(dev["model_count"]),
        "building_floors": safe_int(dev["building_floors"]),
        "shared_amenities": safe_str(dev["shared_amenities"]).split(";") if pd.notna(dev["shared_amenities"]) else [],
        "land_area_m2": safe_float(dev["land_area_m2"]),
        "built_area_m2": safe_float(dev["built_area_m2"]),
        "construction_start_date": safe_str(dev["construction_start_date"]),
        "zone": safe_str(dev["zone"]),
        "location": {
            "lat": safe_float(dev["latitude"]),
            "lng": safe_float(dev["longitude"])
        },
        "models": models_list
    }

    db.developments.update_one(
        {"development_id": doc["development_id"]},
        {"$set": doc},
        upsert=True
    )

print("✔ Datos cargados exitosamente en MongoDB.")


✔ Datos cargados exitosamente en MongoDB.


### Como hacer pequeñas consultas

In [6]:
from pymongo import MongoClient

cliente = MongoClient("mongodb://localhost:27017/")
db = cliente["mazatlan"]

# Ejemplo: ver todos los desarrollos en la zona "Marina"
resultados = db.developments.find({"zone": "Marina"})
for d in resultados:
    print(d["development_name"])


Akkúun Marina Mazatlán
Artemisa Beach Residence
Aruba Grand Marina
Brisas Ocean Club
El Delfín
Ferrara Pacific City
Ferrara Pacific City Torre Sur
Grand Marina Residential & Golf
Isla Veleros
IWA Hotel & Residences Residencias
IWA Hotel & Residences Villas
La Calma Marina Mazatlán
Malia Golf & Yacht
Mangata Golf & Living
Mangata Golf & Living Villas
Mangle Marina & Golf Residences Departamentos
Mangle Marina & Golf Residences Villas
Marina Costa Bonita
Marina Mazatlán Campo de Golf
Nautilus Marina Grand Living
Paseo Golondrinas-Marina Mazatlán
Porto Blanco Golf & Residences Departamentos
Porto Blanco Golf & Residences Villas
Residencial La Dársena
Residencial La Perla
The Lighthouse Marina Plaza
Torre Lamar


### 1. 🔧 Agregar nuevos campos a todos los documentos

Eso agregará el campo "etapa": "" a todos los documentos aunque antes no existiera

In [7]:
# Ejemplo: agregar campo nuevo "etapa" a todos los desarrollos
#db.developments.update_many({}, {"$set": {"etapa": ""}})


### 2. ✏️ Actualizar un campo específico en un desarrollo    

In [8]:
#db.developments.update_one(
    #{"development_id": "DEV001"},
    #{"$set": {"zone": "Norte"}}
#)


### 3. 🧱 Actualizar un campo dentro de un modelo específico

Supón que quieres cambiar los acabados del modelo A1 del desarrollo DEV001:

In [9]:
#db.developments.update_one(
#    {"development_id": "DEV001", "models.model_id": "A1"},
#    {"$set": {"models.$.finishes": "premium"}}
#)


### 4. 🔁 Actualizar múltiples unidades dentro de un modelo

Supón que tus unidades tienen un campo status y quieres cambiarlo:

In [ ]:
#db.developments.update_one(
#    {"development_id": "DEV001"},
#    {"$set": {
#        "models.0.units.0.status": "sold"
#    }}
#)


Para hacer esto dinámicamente, lo ideal sería extraer el documento, modificarlo en Python, y hacer un replace_one.

✅ ¿Recomendación para cambios grandes?
Cuando quieras hacer cambios masivos o estructurales, sigue esta rutina:

Exporta la colección desde Compass o con Python (find() → DataFrame)

Modifica en Python o Excel

Vuelve a subir con un update_one() o replace_one() si reemplazas toda la estructura